## Notebook to make a database of parsed papers 
####    --Containing header or text label

In [8]:
import PyPDF2
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
import re
import os 
import glob

In [9]:
for filename in os.listdir('papers'):
    with open('papers/' + filename,'rb') as pdf_file, open('txts_out/' + filename.split('.')[0] + '.txt', 'w', encoding="utf-8") as text_file:
        read_pdf = PyPDF2.PdfFileReader(pdf_file)
        number_of_pages = read_pdf.getNumPages()
        for page_number in range(number_of_pages):  
            page = read_pdf.getPage(page_number)
            page_content = page.extractText()
            text_file.write(page_content)

Xref table not zero-indexed. ID numbers for objects will be corrected.
Xref table not zero-indexed. ID numbers for objects will be corrected.
Xref table not zero-indexed. ID numbers for objects will be corrected.
Xref table not zero-indexed. ID numbers for objects will be corrected.
Xref table not zero-indexed. ID numbers for objects will be corrected.
Xref table not zero-indexed. ID numbers for objects will be corrected.
Xref table not zero-indexed. ID numbers for objects will be corrected.
Xref table not zero-indexed. ID numbers for objects will be corrected.
Xref table not zero-indexed. ID numbers for objects will be corrected.
Xref table not zero-indexed. ID numbers for objects will be corrected.
Xref table not zero-indexed. ID numbers for objects will be corrected.
Xref table not zero-indexed. ID numbers for objects will be corrected.
Xref table not zero-indexed. ID numbers for objects will be corrected.
Xref table not zero-indexed. ID numbers for objects will be corrected.
Xref t

In [25]:
papers_headers_text_dict = {}
for filename_txt in os.listdir('txts_out'):
# Get raw text
    with open('txts_out/' + filename_txt, 'r', encoding="utf-8") as f:
        read_output = f.readlines()
    last_line = ''
    check_if_numbered = False
    check_if_latin = False
    no_headers_list = []
    headers_list = []
    latin_numbered_list = []
    numberic_numbered_list = []
    math_functions_list = []
    for line_ in read_output:
        if 'Abstract' in line_ or 'ABSTRACT' in line_:
            if '—' in line_:
                line_ = line_.split('—')[0]
            headers_list.append(line_)
        else:
            no_headers_list.append(line_)
        if 'Introduction' in line_ or 'INTRODUCTION' in line_ or 'I NTRODUCTION' in line_:
            if line_[0].isdigit():
                check_if_numbered = True
            elif line_[0] == 'I':
                check_if_latin = True
            else:
                no_headers_list.append(line_)
                break
        if (check_if_numbered and line_[0].isdigit()):
            if ' ' in line_ and len(line_) < 50:
                number_of_digits = sum(c.isdigit() for c in line_)
                if number_of_digits < 3:
                    # print(line_)
                    headers_list.append(line_)
                else:
                    no_headers_list.append(line_)
                    break
        for latin_int_str in ['I.', 'II.', 'III.', 'IV.', 'V.', 'VI.', 'VII.', 'VIII.', 'IX.']:
            if check_if_latin and (line_[0:len(latin_int_str)] == latin_int_str):
                if ' ' in line_ and len(line_) < 90:
                    # print(line_)
                    headers_list.append(line_)
                else:
                    no_headers_list.append(line_)
                    break
        if ' = ' in line_:
            math_functions_list.append(line_)
        latin_numbered_list.append(check_if_latin)
        numberic_numbered_list.append(check_if_numbered)
        last_line = line_
    if True in latin_numbered_list:
        papers_headers_text_dict.update({filename_txt.split('.')[0]: [headers_list, no_headers_list, math_functions_list, True, False]})
    if True in numberic_numbered_list:
        papers_headers_text_dict.update({filename_txt.split('.')[0]: [headers_list, no_headers_list, math_functions_list, False, True]})
    else: 
        papers_headers_text_dict.update({filename_txt.split('.')[0]: [headers_list, no_headers_list, math_functions_list, False, False]})


In [26]:
to_poplist = []
for key_ in papers_headers_text_dict.keys():
    if len(papers_headers_text_dict[key_][0]) < 5:
        to_poplist.append(key_)
    # print(key_, len(papers_headers_text_dict[key_][0]), len(papers_headers_text_dict[key_][1]))
    # print(key_)
    # for header in headers_list:
        # print(header)
for pop_key in to_poplist:
    papers_headers_text_dict.pop(pop_key, None)


In [44]:
import pandas as pd
df = pd.DataFrame(columns=['parsed_line', 'heading_bool', 'source_paper', 'math_bool', 'latin_numbered_bool', 'numberic_numbered_bool'])
for key_ in papers_headers_text_dict.keys():
    for i, header_text in enumerate(papers_headers_text_dict[key_][0]):
        row = {'parsed_line': header_text, 'heading_bool': True, 'source_paper': key_, 'math_bool': False, 'latin_numbered_bool': papers_headers_text_dict[key_][3], 'numberic_numbered_bool': papers_headers_text_dict[key_][4]}
        df = pd.concat([df, pd.DataFrame([row])], axis=0, ignore_index=True) 
    for i, text_line in enumerate(papers_headers_text_dict[key_][1]):
        row = {'parsed_line': text_line, 'heading_bool': False, 'source_paper': key_, 'math_bool': False, 'latin_numbered_bool': papers_headers_text_dict[key_][3], 'numberic_numbered_bool': papers_headers_text_dict[key_][4]}
        df = pd.concat([df, pd.DataFrame([row])], axis=0, ignore_index=True)
    for i, math_line in enumerate(papers_headers_text_dict[key_][2]):
        row = {'parsed_line': text_line, 'heading_bool': False, 'source_paper': key_, 'math_bool': True, 'latin_numbered_bool': papers_headers_text_dict[key_][3], 'numberic_numbered_bool': papers_headers_text_dict[key_][4]}
        df = pd.concat([df, pd.DataFrame([row])], axis=0, ignore_index=True)

C:\Users\TomK2\AppData\Local\Temp/ipykernel_20800/37250557.py:6: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  df = pd.concat([df, pd.DataFrame([row])], axis=0, ignore_index=True)
C:\Users\TomK2\AppData\Local\Temp/ipykernel_20800/37250557.py:6: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  df = pd.concat([df, pd.DataFrame([row])], axis=0, ignore_index=True)
C:\Users\TomK2\AppData\Local\Temp/ipykernel_20800/37250557.py:6: FutureWarning: In a future version, object-dtype columns with all-bool values will not be included in reductions with bool_only=True. Explicitly cast to bool dtype instead.
  df = pd.concat([df, pd.DataFrame([row])], axis=0, ignore_index=True)
C:\Users\TomK2\AppData\Local\Temp/ipykernel_20800/37250557.py:6: FutureWa

In [27]:
for key_ in papers_headers_text_dict.keys():
    print(key_, len(papers_headers_text_dict[key_][0]), len(papers_headers_text_dict[key_][1]), len(papers_headers_text_dict[key_][2]), papers_headers_text_dict[key_][3], papers_headers_text_dict[key_][4])
 

1802 5 216 0 False True
188130647 7 386 3 False False
2012_Book_AmbientIntelligence 13 511 0 False True
29020-59012-1-PB 10 421 0 False True
A BERT-Based Transfer Learning Approach for 11 526 1 False True
Adversarial Attacks on Deep-learning Models in Natural 6 353 0 False True
AnalysisOfShoppingBehaviorBasedOnSurveilanceSystem 7 550 0 False False
A_Broadband_High_Common_Mode_Rejection_Ratio_Instrumentation_Amplifier 6 325 0 False False
A_Review_of_Face_Recognition_Technology 8 988 0 False False
ChatbotsInABotnetWorld 9 359 1 False True
Complex Word Identification Convolutional Neural Network vs Feature Engineering 9 245 0 False True
conninePinnow 11 278 1 False True
Context-Based_Feature_Technique_for_Sarcasm_Identification_in_Benchmark_Datasets_Using_Deep_Learning_and_BERT_Model 7 1546 0 False False
Cross-Lingual Transfer Learning for Complex word Identification 5 359 1 False False
DeepSonar 14 528 0 False True
DennisVlaar_Paper 6 477 0 False False
dijkstra2002 9 614 0 False True
DNN

In [42]:
df.sample(10)

parsed_line heading_bool  \
15007  Jerod Weinman, Andras Ferencz, Paul Dickson, D...        False   
21997  corporation. It consists of 619446 emails from...        False   
19555  where the sum runs over all panels ,is the cen...        False   
8868   reasoning abilities, the answers are often inc...        False   
9752   Fig.16Camerapositionwithgroupoffrontalview.The...        False   
4080   local perception GAN for photorealistic and id...        False   
2729   in the fusion process. Furthermore each modali...        False   
3380   perspectives. The paper describes the developm...        False   
7498   Gauge [ 28] introduce neuron coverage as testi...        False   
11536  Manuscript received 19 Jan. 2006; revised 5 Ju...        False   

                                            source_paper math_bool  \
15007                                          lfw_paper     False   
21997                                  targeted_phishing     False   
19555                                              pub07     False   
8868                                  DNNvsSecondGraders     False   
9752   Evaluating effects of focal length and viewing...     False   
4080             A_Review_of_Face_Recognition_Technology     False   
2729   AnalysisOfShoppingBehaviorBasedOnSurveilanceSy...     False   
3380             A_Review_of_Face_Recognition_Technology     False   
7498                                           DeepSonar     False   
11536                                              i0671     False   

      latin_numbered_bool numberic_numbered_bool  
15007               False                  False  
21997               False                  False  
19555               False                  False  
8868                False                   True  
9752                False                   True  
4080                False                  False  
2729                False                  False  
3380                False                  False  
7498                False                   True  
11536               False                   True